# Mapping Data with Folium

![](images/folium.png)

Below, we will go through a brief introduction to the **Folium** library.  This is a nice way to build interactive visuzlizations.  We will be executing these in the jupyter notebooks, however they are easily output as `.html` files ready to be served.  To begin, let's make sure we have folium installed.  

In [2]:
import folium
import pandas as pd

We can make basic maps centered at any geolocation.  For example, below we create a basic map of Portland, Oregon.  

In [3]:
m = folium.Map(location=[45.5236, -122.6750])

In [4]:
m

In [5]:
m.save('index_map.html')

We can add arguments that include changing the style of the map and the initial zoom level.

In [6]:
folium.Map(
    location=[45.5236, -122.6750],
    tiles='Stamen Toner',
    zoom_start=13
)

We can use the `popup` argument to include information to be displayed at specified marker locations.

In [7]:
tooltip = 'Click me!'
m = folium.Map(
    location=[45.372, -121.6972],
    zoom_start=12,
    tiles='Stamen Terrain'
)



folium.Marker([45.3288, -121.6625], popup='<i>Mt. Hood Meadows</i>').add_to(m)
folium.Marker([45.3311, -121.7113], popup='<b>Timberline Lodge</b>').add_to(m)
m

We can even include `markdown` syntax and icons.

In [8]:
m = folium.Map(
    location=[45.372, -121.6972],
    zoom_start=12,
    tiles='Stamen Terrain'
)

folium.Marker(
    location=[45.3288, -121.6625],
    popup='Mt. Hood Meadows',
    icon=folium.Icon(icon='cloud')
).add_to(m)

folium.Marker(
    location=[45.3311, -121.7113],
    popup='Timberline Lodge',
    icon=folium.Icon(color='green')
).add_to(m)

folium.Marker(
    location=[45.3300, -121.6823],
    popup='Some Other Location',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

In [9]:
m

We can manually control radii for markers of interest.  Below, we plot two circles at specific locations.

In [10]:
m = folium.Map(
    location=[45.5236, -122.6750],
    tiles='Stamen Toner',
    zoom_start=13
)

folium.Circle(
    radius=100,
    location=[45.5244, -122.6699],
    popup='The Waterfront',
    color='crimson',
    fill=False,
).add_to(m)

folium.CircleMarker(
    location=[45.5215, -122.6261],
    radius=50,
    popup='Laurelhurst Park',
    color='#3186cc',
    fill=True,
    fill_color='#3186cc'
).add_to(m)


In [11]:
m

### Mapping Bike Data

Now, we will use a dataset from NYC's citibike data.  Our goal is to compare incoming and outgoing traffic at given stations depending on the time of day.  

In [19]:
folium_map = folium.Map(location=[40.738, -73.98],
                        zoom_start=13,
                        tiles="CartoDB dark_matter")
marker = folium.CircleMarker(location=[40.738, -73.98])
marker.add_to(folium_map)

In [20]:
folium_map

In [36]:
bikes = pd.read_csv('data/201306-citibike-tripdata.csv')

In [37]:
bikes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 577703 entries, 0 to 577702
Data columns (total 15 columns):
tripduration               577703 non-null int64
starttime                  577703 non-null object
stoptime                   577703 non-null object
start station id           577703 non-null int64
start station name         577703 non-null object
start station latitude     577703 non-null float64
start station longitude    577703 non-null float64
end station id             559644 non-null float64
end station name           559644 non-null object
end station latitude       559644 non-null float64
end station longitude      559644 non-null float64
bikeid                     577703 non-null int64
usertype                   577703 non-null object
birth year                 337382 non-null float64
gender                     577703 non-null int64
dtypes: float64(6), int64(4), object(5)
memory usage: 66.1+ MB


In [64]:
bikes['starttime'] = pd.to_datetime(bikes['starttime'])
bikes['stoptime'] = pd.to_datetime(bikes['stoptime'])
bikes['hour'] = bikes['starttime'].map(lambda x: x.hour)
bikes['ehour'] = bikes['stoptime'].map(lambda x: x.hour)

In [39]:
bikes.head()

tripduration           starttime            stoptime  start station id  \
0           695 2013-06-01 00:00:01 2013-06-01 00:11:36               444   
1           693 2013-06-01 00:00:08 2013-06-01 00:11:41               444   
2          2059 2013-06-01 00:00:44 2013-06-01 00:35:03               406   
3           123 2013-06-01 00:01:04 2013-06-01 00:03:07               475   
4          1521 2013-06-01 00:01:22 2013-06-01 00:26:43              2008   

       start station name  start station latitude  start station longitude  \
0      Broadway & W 24 St               40.742354               -73.989151   
1      Broadway & W 24 St               40.742354               -73.989151   
2  Hicks St & Montague St               40.695128               -73.995951   
3     E 15 St & Irving Pl               40.735243               -73.987586   
4   Little West St & 1 Pl               40.705693               -74.016777   

   end station id        end station name  end station latitude  \
0           434.0         9 Ave & W 18 St             40.743174   
1           434.0         9 Ave & W 18 St             40.743174   
2           406.0  Hicks St & Montague St             40.695128   
3           262.0         Washington Park             40.691782   
4           310.0     State St & Smith St             40.689269   

   end station longitude  bikeid    usertype  birth year  gender  hour  
0             -74.003664   19678  Subscriber      1983.0       1     0  
1             -74.003664   16649  Subscriber      1984.0       1     0  
2             -73.995951   19599    Customer         NaN       0     0  
3             -73.973730   16352  Subscriber      1960.0       1     0  
4             -73.989129   15567  Subscriber      1983.0       1     0

In [40]:
locations = bikes.groupby('start station id').first()

In [41]:
locations = locations.loc[:, ["start station latitude", "start station longitude", "start station name"]]

In [42]:
subset = bikes[bikes["hour"]==10]

In [43]:
dept_counts = subset.groupby("start station id").count()

In [44]:
dept_counts = dept_counts.iloc[:, [0]]

In [45]:
dept_counts.columns = ["Departure Counts"]

### Problem

Repeat the above for arrivals, in anticipation of joining the two for our map.

In [65]:
locations2 = bikes.groupby('end station id').first()

In [66]:
locations2 = locations2.loc[:, ["end station latitude", "end station longitude", "end station name"]]

In [67]:
subset = bikes[bikes["ehour"]==10]

In [68]:
arr_counts = subset.groupby("end station id").count()

In [69]:
arr_counts = arr_counts.iloc[:, [0]]

In [70]:
arr_counts.columns = ["Arrival Counts"]

In [71]:
trip_counts = dept_counts.join(locations).join(arr_counts)

In [74]:
trip_counts.head()

Departure Counts  start station latitude  \
start station id                                             
72                              80               40.767272   
79                             117               40.719116   
82                              25               40.711174   
83                              44               40.683826   
116                            115               40.741776   

                  start station longitude             start station name  \
start station id                                                           
72                             -73.993929               W 52 St & 11 Ave   
79                             -74.006667       Franklin St & W Broadway   
82                             -74.000165         St James Pl & Pearl St   
83                             -73.976323  Atlantic Ave & Fort Greene Pl   
116                            -74.001497                W 17 St & 8 Ave   

                  Arrival Counts  
start station id                  
72                            65  
79                           157  
82                            17  
83                            61  
116                          132

In [72]:
for index, row in trip_counts.iterrows():
    
    net_departures = (row["Departure Counts"]-row["Arrival Counts"])
    
    radius = net_departures/7
    
    if net_departures>0:
        color="#E37222" # tangerine
    else:
        color="#0A8A9F" # teal
    
    folium.CircleMarker(location=(row["start station latitude"],
                                  row["start station longitude"]),
                        radius=radius,
                        color=color,
                        fill=True).add_to(folium_map)

In [73]:
folium_map

In [75]:
popup_text = """{}<br>
                total departures: {}<br> 
                total arrivals: {}<br>
                net departures: {}"""


popup_text = popup_text.format(row["start station name"],
                               row["Arrival Counts"],
                               row["Departure Counts"],
                               net_departures)

In [76]:
for index, row in trip_counts.iterrows():
    net_departures = (row["Departure Counts"]-row["Arrival Counts"])
    radius = net_departures/7
    if net_departures>0:
        color="#E37222" # tangerine
    else:
        color="#0A8A9F" # teal
    
    folium.CircleMarker(location=(row["start station latitude"],
                                  row["start station longitude"]),
                        radius=radius,
                        color=color,
                        fill=True, popup = popup_text).add_to(folium_map)

In [77]:
folium_map

### PROBLEM

Compare this image to that of when people are leaving work.  Doe you see what you expect?  What does this tell you about movement in the city?

In [79]:
locations3 = bikes.groupby('start station id').first()
locations3 = locations3.loc[:, ["start station latitude", "start station longitude", "start station name"]]
subset = bikes[bikes["hour"]==18]
dept_counts2 = subset.groupby("start station id").count()
dept_counts2 = dept_counts2.iloc[:, [0]]
dept_counts2.columns = ["Departure Counts"]

In [80]:
locations4 = bikes.groupby('end station id').first()
locations4 = locations2.loc[:, ["end station latitude", "end station longitude", "end station name"]]
subset = bikes[bikes["hour"]==18]
arr_counts2 = subset.groupby("end station id").count()
arr_counts2 = arr_counts2.iloc[:, [0]]
arr_counts2.columns = ["Arrival Counts"]

In [81]:
trip_counts2 = dept_counts2.join(locations3).join(arr_counts2)

In [82]:
trip_counts2.head()

Departure Counts  start station latitude  \
start station id                                             
72                             187               40.767272   
79                             403               40.719116   
82                              76               40.711174   
83                             111               40.683826   
116                            215               40.741776   

                  start station longitude             start station name  \
start station id                                                           
72                             -73.993929               W 52 St & 11 Ave   
79                             -74.006667       Franklin St & W Broadway   
82                             -74.000165         St James Pl & Pearl St   
83                             -73.976323  Atlantic Ave & Fort Greene Pl   
116                            -74.001497                W 17 St & 8 Ave   

                  Arrival Counts  
start station id                  
72                           186  
79                           325  
82                            58  
83                           167  
116                          207

In [83]:
for index, row in trip_counts2.iterrows():
    
    net_departures2 = (row["Departure Counts"]-row["Arrival Counts"])
    
    radius = net_departures2/7
    
    if net_departures2>0:
        color="#E37222" # tangerine
    else:
        color="#0A8A9F" # teal
    
    folium.CircleMarker(location=(row["start station latitude"],
                                  row["start station longitude"]),
                        radius=radius,
                        color=color,
                        fill=True).add_to(folium_map)

In [84]:
folium_map

In [90]:
popup_text = """{}<br>
                total departures: {}<br> 
                total arrivals: {}<br>
                net departures: {}"""


popup_text = popup_text.format(row["start station name"],
                               row["Arrival Counts"],
                               row["Departure Counts"],
                               net_departures)

In [91]:
for index, row in trip_counts2.iterrows():
    net_departures2 = (row["Departure Counts"]-row["Arrival Counts"])
    radius = net_departures2/7
    if net_departures2>0:
        color="#E37222" # tangerine
    else:
        color="#0A8A9F" # teal
    
    folium.CircleMarker(location=(row["start station latitude"],
                                  row["start station longitude"]),
                        radius=radius,
                        color=color,
                        fill=True, popup = popup_text).add_to(folium_map)

In [92]:
folium_map

In [ ]:
locations2 = bikes.groupby('end station id').first()
locations2 = locations2.loc[:, ["end station latitude", "end station longitude", "end station name"]]
subset = bikes[bikes["hour"]==10]
arr_counts = subset.groupby("end station id").count()
arr_counts = arr_counts.iloc[:, [0]]
arr_counts.columns = ["Arrival Counts"]